In [12]:
import gymnasium as gym
from pogema import GridConfig
from stable_baselines3 import DQN, A2C
from stable_baselines3.common.evaluation import evaluate_policy

%load_ext autoreload
%autoreload 2
%matplotlib inline

grid_config = GridConfig(
    size=8,
    density=0.3,
    num_agents=1,
    max_episode_steps=128,
    obs_radius=3
)

env = gym.make("Pogema-v0",grid_config=grid_config)

a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1
)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


#### Optuna Integration

In [13]:
""" Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using A2C implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python sb3_simple.py

"""
from typing import Any
from typing import Dict

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import A2C
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.monitor import Monitor
import torch
import torch.nn as nn


N_TRIALS = 100
N_STARTUP_TRIALS = 5
N_EVALUATIONS = 2
N_TIMESTEPS = int(5.0e5)
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 3


DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "verbose": 1,
    "env": env
}

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """Sampler for A2C hyperparameters."""
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)

    trial.set_user_attr("gamma", gamma)

    return {
        "gamma": gamma,
        "learning_rate": learning_rate,
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model.
    model = A2C(**kwargs)
    # Create env used for evaluation.
    eval_env = Monitor(env)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env, trial, n_eval_episodes=N_EVAL_EPISODES, eval_freq=EVAL_FREQ, deterministic=True
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3)

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, n_jobs=4, timeout=600)
    except KeyboardInterrupt:
        pass

    print("Number of finished trials: ", len(study.trials))

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print("    {}: {}".format(key, value))


[I 2023-11-10 16:33:01,429] A new study created in memory with name: no-name-13378f38-0a9a-4cc9-b846-8cc45e8d1090
[W ParallelNative.cpp:230] Warning: Cannot set number of intraop threads after parallel work has started or after set_num_threads call when using native parallel backend (function set_num_threads)


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 103      |
|    ep_rew_mean        | 0.25     |
| time/                 |          |
|    fps                | 164      |
|    iterations         | 100      |
|    time_elapsed       | 3        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -1.61    |
|    explained_variance | -109     |
|    learning_rate      | 0.000235 |
|    n_updates          | 99       |
|    policy_loss        | 0.339    |
|    value_loss         | 0.0796   |
--------------------------------

[I 2023-11-10 17:17:32,890] Trial 3 finished with value: 1.0 and parameters: {'gamma': 0.09484641388147239, 'lr': 0.00023454706232122486}. Best is trial 3 with value: 1.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 147       |
|    ep_rew_mean        | 0         |
| time/                 |           |
|    fps                | 179       |
|    iterations         | 95900     |
|    time_elapsed       | 2672      |
|    total_timesteps    | 479500    |
| train/                |           |
|    entropy_loss       | -7.49e-17 |
|    explained_variance | nan       |
|    learning_rate      | 0.132     |
|    n_updates          | 95899     |
|    policy_loss        | -0        |
|    value_loss         | 0         |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 84.4      |
|    ep_rew_mean        | 0.37      |
| time/                 |           |
|    fps                | 179       |
|    iterations         | 95800     |
|    time_elapsed       | 2672      |
|    total_timesteps    | 479000    |
| train/    

[I 2023-11-10 17:18:37,152] Trial 1 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.000123319250744272, 'lr': 0.5622487326008988}. Best is trial 3 with value: 1.0.


-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 134       |
|    ep_rew_mean        | 0         |
| time/                 |           |
|    fps                | 181       |
|    iterations         | 99400     |
|    time_elapsed       | 2735      |
|    total_timesteps    | 497000    |
| train/                |           |
|    entropy_loss       | -1.15e-16 |
|    explained_variance | nan       |
|    learning_rate      | 0.132     |
|    n_updates          | 99399     |
|    policy_loss        | -0        |
|    value_loss         | 0         |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 109       |
|    ep_rew_mean        | 0.2       |
| time/                 |           |
|    fps                | 181       |
|    iterations         | 99400     |
|    time_elapsed       | 2736      |
|    total_timesteps    | 497000    |
| train/    

[I 2023-11-10 17:18:43,350] Trial 2 finished with value: 0.0 and parameters: {'gamma': 0.0001980283364452409, 'lr': 0.13150202766270055}. Best is trial 3 with value: 1.0.


-------------------------------------
| eval/                 |           |
|    mean_ep_length     | 128       |
|    mean_reward        | 0         |
| time/                 |           |
|    total_timesteps    | 500000    |
| train/                |           |
|    entropy_loss       | -8.91e-20 |
|    explained_variance | -1.19e-07 |
|    learning_rate      | 0.0963    |
|    n_updates          | 99999     |
|    policy_loss        | -0        |
|    value_loss         | 1.5e-07   |
-------------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 116      |
|    ep_rew_mean     | 0.18     |
| time/              |          |
|    fps             | 182      |
|    iterations      | 100000   |
|    time_elapsed    | 2742     |
|    total_timesteps | 500000   |
---------------------------------


[I 2023-11-10 17:18:43,690] Trial 0 finished with value: 0.0 and parameters: {'gamma': 0.0004469550583477574, 'lr': 0.0963085409238121}. Best is trial 3 with value: 1.0.


Number of finished trials:  4
Best trial:
  Value:  1.0
  Params: 
    gamma: 0.09484641388147239
    lr: 0.00023454706232122486
  User attrs:
    gamma: 0.9051535861185276


### Train agent with best hyper parameters

In [14]:
a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1,
    gamma=1-0.09484641388147239,#0.0033700061384865873,
    learning_rate=0.00023454706232122486#0.08419759274683712,
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [15]:
# Train agent and save it
a2c_model.learn(int(5.0e5))
a2c_model.save("saved/a2c_c")

------------------------------------
| rollout/              |          |
|    ep_len_mean        | 70.7     |
|    ep_rew_mean        | 0.571    |
| time/                 |          |
|    fps                | 1410     |
|    iterations         | 100      |
|    time_elapsed       | 0        |
|    total_timesteps    | 500      |
| train/                |          |
|    entropy_loss       | -1.6     |
|    explained_variance | -3.46    |
|    learning_rate      | 0.000235 |
|    n_updates          | 99       |
|    policy_loss        | 0.947    |
|    value_loss         | 0.415    |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 87.9     |
|    ep_rew_mean        | 0.4      |
| time/                 |          |
|    fps                | 1233     |
|    iterations         | 200      |
|    time_elapsed       | 0        |
|    total_timesteps    | 1000     |
| train/                |          |
|

#### Testing 

In [16]:
a2c_model = A2C.load("saved/a2c_c")

env.reset()

mean_reward, std_reward = evaluate_policy(a2c_model, env, deterministic=True, n_eval_episodes=20)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

mean_reward:0.70 +/- 0.46


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


In [20]:
# RANDOM SEED
from IPython.display import SVG, display
from pogema.animation import AnimationMonitor, AnimationConfig

env = AnimationMonitor(env)

def evaluate_success_rate(model, env, num_episodes=1000):
    success_count = 0
    step_array = []
    for i in range(num_episodes):
        print(f'---{i}---')
        obs = env.reset()

        # Check if observation is a tuple and extract the first element if true.
        if isinstance(obs, tuple):
            obs = obs[0]
        max_step = 128
        steps_taken = 0
        done = truncated = False
        while not done and max_step > 0:
            action, _ = model.predict(obs)
            next_obs, reward, done, truncated, info = env.step(action)
            print(action,max_step,success_count,done)
            max_step -= 1
            steps_taken += 1
            # Check if next_obs is a tuple and extract the first element if true.
            if isinstance(next_obs, tuple):
                next_obs = next_obs[0]
            obs = next_obs

            # Check if agent was successful in that episode.
            if done:
                success_count += 1
                step_array.append(steps_taken)
                env.save_animation(f"media_c/render{i}.svg", AnimationConfig(egocentric_idx=0))
                break

    success_rate = success_count / num_episodes
    return success_rate, step_array

success_rate,step_array = evaluate_success_rate(a2c_model, env)
print(f"Agent Success Rate: {success_rate * 100:.2f}%")
print(f"steps to termination : {step_array}")

---0---
4 128 0 False
4 127 0 False
2 126 0 False
1 125 0 False
2 124 0 False
1 123 0 False
2 122 0 False
1 121 0 False
2 120 0 False
1 119 0 False
2 118 0 False
1 117 0 False
2 116 0 False
1 115 0 False
2 114 0 False
1 113 0 False
2 112 0 False
1 111 0 False
2 110 0 False
1 109 0 False
2 108 0 False
1 107 0 False
2 106 0 False
2 105 0 False
1 104 0 False
2 103 0 False
1 102 0 False
2 101 0 False
1 100 0 False
2 99 0 False
1 98 0 False
2 97 0 False
1 96 0 False
2 95 0 False
1 94 0 False
2 93 0 False
2 92 0 False
1 91 0 False
2 90 0 False
1 89 0 False
2 88 0 False
1 87 0 False
2 86 0 False
1 85 0 False
2 84 0 False
1 83 0 False
2 82 0 False
1 81 0 False
2 80 0 False
1 79 0 False
2 78 0 False
1 77 0 False
2 76 0 False
1 75 0 False
2 74 0 False
1 73 0 False
2 72 0 False
1 71 0 False
2 70 0 False
1 69 0 False
2 68 0 False
1 67 0 False
2 66 0 False
1 65 0 False
2 64 0 False
1 63 0 False
2 62 0 False
0 61 0 False
1 60 0 False
2 59 0 False
1 58 0 False
2 57 0 False
1 56 0 False
2 55 0 False
1

In [21]:
step_array

[12,
 1,
 12,
 8,
 2,
 5,
 2,
 5,
 4,
 2,
 3,
 6,
 2,
 5,
 3,
 2,
 9,
 10,
 5,
 9,
 3,
 3,
 11,
 4,
 5,
 2,
 3,
 8,
 1,
 5,
 1,
 114,
 3,
 2,
 4,
 11,
 5,
 4,
 6,
 4,
 1,
 11,
 11,
 7,
 96,
 1,
 3,
 6,
 5,
 6,
 2,
 6,
 7,
 5,
 2,
 3,
 6,
 1,
 9,
 33,
 3,
 2,
 3,
 4,
 46,
 7,
 13,
 3,
 10,
 4,
 4,
 4,
 4,
 7,
 5,
 4,
 3,
 1,
 1,
 6,
 9,
 1,
 3,
 8,
 7,
 2,
 94,
 3,
 18,
 9,
 6,
 6,
 7,
 18,
 1,
 2,
 9,
 17,
 5,
 1,
 10,
 12,
 5,
 3,
 4,
 2,
 4,
 7,
 1,
 2,
 6,
 7,
 8,
 6,
 5,
 1,
 12,
 2,
 3,
 6,
 5,
 1,
 10,
 8,
 4,
 6,
 5,
 4,
 10,
 11,
 3,
 1,
 1,
 9,
 1,
 3,
 6,
 7,
 5,
 3,
 7,
 2,
 6,
 1,
 3,
 6,
 1,
 5,
 5,
 2,
 3,
 6,
 9,
 4,
 7,
 1,
 13,
 5,
 4,
 1,
 7,
 6,
 10,
 4,
 1,
 3,
 3,
 6,
 3,
 7,
 3,
 3,
 4,
 6,
 3,
 2,
 2,
 6,
 7,
 4,
 1,
 5,
 9,
 3,
 7,
 2,
 7,
 7,
 6,
 11,
 5,
 1,
 1,
 3,
 6,
 7,
 7,
 24,
 4,
 8,
 8,
 5,
 8,
 3,
 1,
 3,
 3,
 6,
 10,
 4,
 46,
 14,
 3,
 5,
 3,
 5,
 6,
 12,
 6,
 4,
 3,
 6,
 3,
 5,
 10,
 3,
 5,
 8,
 5,
 1,
 3,
 2,
 8,
 112,
 10,
 14,
 1,
 5,
 1,
 9,
 95

In [22]:
import numpy as np
np.mean(step_array)

7.922818791946309

In [23]:
from IPython.display import SVG, display
from utils.util import *

MODEL_NAME = f"saved/a2c_c"
MAX_EPISODE_STEPS = 128
MAX_TRIALS = 1000
SAVE_METRICS_PATH = 'saved/evaluation_metrics.yml'


metrics = evaluate_metrics(a2c_model, env, MODEL_NAME, num_episodes=MAX_EPISODE_STEPS, num_trials=MAX_TRIALS, verbose=False, save_animation=False)
save_metrics(metrics, MODEL_NAME, SAVE_METRICS_PATH)
print(f"Agent Success Rate: {metrics['success_rate'] * 100:.2f}%")
print(f"Steps to termination : {metrics['step_array']}")
print(f"Average steps to termination : {metrics['ave_steps']}")

Agent Success Rate: 88.20%
Steps to termination : [11, 2, 5, 3, 6, 8, 11, 7, 3, 5, 5, 1, 2, 13, 11, 1, 2, 3, 125, 9, 4, 6, 19, 2, 33, 1, 9, 53, 10, 19, 7, 31, 7, 3, 5, 7, 4, 1, 2, 5, 7, 1, 5, 4, 3, 3, 22, 3, 4, 7, 2, 4, 1, 2, 3, 7, 3, 6, 5, 29, 6, 4, 1, 4, 7, 5, 3, 10, 5, 11, 1, 3, 4, 4, 5, 88, 4, 6, 7, 7, 5, 9, 62, 7, 2, 9, 3, 1, 5, 4, 10, 5, 6, 5, 75, 1, 4, 7, 8, 8, 6, 10, 15, 2, 5, 10, 12, 23, 7, 3, 7, 1, 2, 5, 3, 6, 4, 4, 3, 4, 6, 3, 1, 7, 5, 1, 6, 1, 4, 14, 2, 4, 2, 1, 2, 1, 8, 1, 3, 7, 1, 12, 2, 2, 6, 9, 6, 6, 7, 7, 6, 1, 1, 7, 7, 7, 4, 9, 6, 3, 4, 1, 8, 19, 6, 4, 1, 26, 2, 6, 5, 18, 2, 10, 5, 3, 12, 4, 7, 3, 30, 1, 2, 10, 37, 6, 18, 1, 1, 8, 8, 1, 2, 4, 3, 3, 89, 9, 1, 6, 11, 7, 4, 10, 2, 5, 2, 58, 5, 1, 1, 6, 7, 4, 7, 1, 2, 10, 8, 6, 6, 35, 2, 14, 5, 6, 2, 14, 2, 1, 4, 11, 1, 4, 3, 7, 4, 4, 3, 10, 7, 63, 4, 4, 3, 1, 6, 6, 4, 4, 2, 3, 8, 6, 7, 2, 2, 4, 4, 14, 4, 10, 4, 14, 62, 3, 7, 4, 2, 3, 3, 4, 14, 1, 107, 93, 6, 3, 4, 3, 6, 1, 5, 23, 5, 3, 1, 2, 5, 10, 1, 5, 8, 4, 1, 2, 2, 8